In [1]:

# load data
from sentence_transformers import SentenceTransformer
from twitter.data.loader.prepro import get_user, get_cleaned_tweets, get_user_df

from bertopic import BERTopic

model = SentenceTransformer('paraphrase-MiniLM-L3-v2')


data = get_cleaned_tweets("BabakShekarabi")
data = data.to_list()

2023-04-12 17:44:55.566195: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-04-12 17:44:57.030477: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
2023-04-12 17:44:59.369951: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:997] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2023-04-12 17:44:59.546531: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:997] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA n

In [2]:
labels = ['Joy', 'Sadness', 'Anger', 'Fear', 'Disgust', 'Surprise', 'Amusement', 'Contempt',
          'Contentment', 'Embarrassment', 'Excitement', 'Guilt',
          'Pride in achievement', 'Relief', 'Satisfaction', 'Sensory pleasure',
          'Shame', 'Aesthetic experience', 'Anxiety', 'Compassion', 'Depression', 'Envy', 'Fright', 'Gratitude', 'Hope', 'Jealousy', 'Love']


In [18]:

seed_topic_list = [["رضاخان", "جاوید", "پاینده", "شاه"],
                   ["شاهزاده", "رضا", "تنها", "پهلوی"],
                   ["تشکر", "سپاس", "ارادت", "درود"]]

In [21]:
#data = get_cleaned_tweets("BabakShekarabi")

topic_model = BERTopic(embedding_model=model, calculate_probabilities=True, verbose=True,
                       seed_topic_list=seed_topic_list
                       )
embeddings = model.encode(data, show_progress_bar=False)
topics, probabilities = topic_model.fit_transform(data, embeddings)


Batches:   0%|          | 0/1 [00:00<?, ?it/s]

2023-04-12 18:20:10,475 - BERTopic - Reduced dimensionality
2023-04-12 18:20:12,642 - BERTopic - Clustered reduced embeddings


In [22]:
topic_model.visualize_topics()

In [6]:
embeddings = model.encode(data, show_progress_bar=False)

In [17]:
topic_model.visualize_documents(data, embeddings=embeddings)

In [11]:
from umap import UMAP
from hdbscan import HDBSCAN

reduced_embeddings = UMAP(n_neighbors=15, n_components=5, metric='cosine').fit_transform(embeddings)
hdbscan_model = HDBSCAN(min_cluster_size=10, metric='euclidean', prediction_data=True)
topic_model = BERTopic(hdbscan_model=hdbscan_model,embedding_model=model).fit(data)
topic_model.visualize_documents(data)

2023-04-12 17:47:54,837 - BERTopic - Transformed documents to Embeddings
2023-04-12 17:48:06,387 - BERTopic - Reduced dimensionality
2023-04-12 17:48:06,567 - BERTopic - Clustered reduced embeddings


In [19]:
topic_model = BERTopic(hdbscan_model=hdbscan_model,embedding_model=model, n_gram_range=(1,2), min_topic_size=10, nr_topics=10).fit(data)
topic_model.visualize_documents(data)

In [28]:
topic_model.visualize_hierarchy()